In [10]:
#IMPORTANT------

#RandomContrast must be turned off in augmentation model for below
#sections to work. RandomContrast does not have a built in gradient 
#calculation method so cells below will throw exceptions if not disabled

#Written by JW

#Following tutorial by Chollet, F. (2020, May 29). Visualizing what convnets learn. Keras. 
#Retrieved December 19, 2022, from https://keras.io/examples/vision/visualizing_what_convnets_learn/ 

In [58]:
#Import libraries
import matplotlib as plt
import numpy as np
import tensorflow as tf
from tensorflow import keras
from keras.models import load_model

#Set constants
imgWidth = 360
imgHeight = 360

#The layer to make images for name should match name field of trained model
layerName = "conv3"

#Testing
model = load_model('trainedModel.h5')

#Get the layer from the trained model
layer = model.get_layer(layerName)

#Get the features from the trained model
features = keras.Model(inputs = model.inputs, outputs = layer.output)

In [29]:
#Function to compute the loss for a given image and filter
def calculateLoss(img, indx):
    
    #Evaluate model on this image and get output of desired layer
    response = features(img)
    
    #response = model(img)
    
    #Get the features of filter indx and remove 2px from edges of image
    filterResponse = response[:, 2:-2, 2:-2, indx]
    
    #Return the mean of the selected filter features
    return tf.reduce_mean(filterResponse)

In [30]:
#Function defining a single step in gradient ascent process
@tf.function
def ascend(img, indx, lRate):
    
    #TensorFlow GradientTape will watch for changes in model weights as an image passes through
    with tf.GradientTape() as tape:
        tape.watch(img)
        
        #Find the loss for this image and filter
        loss = calculateLoss(img, indx)
    
    #Compute gradient and compute Euclidian norm
    gradient = tape.gradient(loss, img)
    gradient = tf.math.l2_normalize(gradient)
    
    #Modify the image pixels by a multiple of the computed gradient
    img += (lRate * gradient)
    
    #Return computed loss and the modified image
    return loss, img

In [52]:
#Function to generate a random image
def randomImage():
    
    #Image containing random pixel values from uniform distribution in 8bit RGB format
    img = tf.random.uniform(shape = (1, imgWidth, imgHeight, 3), minval = .125, maxval = .25)
   
    return img

In [32]:
#Function to create image for filter visualization
def createFilterImage(indx):
    
    #Number of iterations
    n = 30
    
    #Learning rate
    lRate = 10.0
    
    #Get random initial image
    img = randomImage()
    
    #Ascend n number of steps
    for i in range(n):
        loss, img = ascend(img, indx, lRate)
    
    #Process the image created from ascent loop
    img = createImage(img[0].numpy())
    
    #Return loss and created image
    return loss, img

In [33]:
#Function to create and scale image
def createImage(img):
    #Scale image using Z-Score of distance from mean
    img -= img.mean()
    img /= img.std() + 1e-5
    
    #Make variance .15
    img *= .15
    
    #Remove edges of image
    img = img[25:-25, 25:-25, :]
    
    #Move mean to 1/2
    img += .5
    
    #Remove values outside of [0,1]
    img = np.clip(img, 0, 1)
    
    #Transform to 8-bit RGB format
    img *= 255
    img = np.clip(img, 0, 255).astype("uint8")
    
    #Return the created image
    return img

In [60]:
#Import library for image display
import matplotlib.pyplot as plt

#Number of filter images to make
numImg = 9

#Store created filter images
filterImages = []

#Make numImg of filter images
for i in range(numImg):
    
    #Call above functions
    loss, img = createFilterImage(i)
    
    #Add to list
    filterImages.append(img)

#Plot the images
plt.figure(figsize=(150, 150))
for images in filterImages:
    for i in range(numImg):
        
        #Add current image to square grid. Dimension must be sqrt(numImg)xsqrt(numImg)
        ax = plt.subplot(3, 3, i + 1)
        
        #8bit per channel colors
        plt.imshow(filterImages[i].astype("uint8"))
        plt.axis("off")